In [232]:
import pandas as pd
import numpy as np
import re
import math

# Plotting libraries
import matplotlib.pyplot as plt
import seaborn as sns

# Import natural language processing libraries
import nltk
from sklearn.feature_extraction.text import CountVectorizer

# Model selection libraries
from sklearn.model_selection import train_test_split, GridSearchCV

# Processing libraries
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.compose import ColumnTransformer

# Modeling libraries
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier

# Model Evaluation Libraries
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay

# Import Dimensionality Reduction libraries
from sklearn.decomposition import PCA

# Import pipeline library
from sklearn.pipeline import Pipeline

from tempfile import mkdtemp

In [233]:
# Import warnings and supress them
import warnings
warnings.filterwarnings('ignore')

In [246]:
# Configure Pandas to show all columns / rows
pd.options.display.max_columns = 2000
pd.options.display.max_rows = 2000

In [235]:
# Set up matplotlib to use nice styles
plt.style.use('ggplot')

In [236]:
# Load data from phishing email csv
email_df = pd.read_csv('./data/phishing_all_data_clean_1.csv')

In [237]:
email_df.shape

(13025, 5)

In [238]:
email_df['phishing'].value_counts()

0    7157
1    5868
Name: phishing, dtype: int64

In [240]:
X = email_df.drop(columns=['phishing'])
y = email_df.loc[:, ['phishing']]

In [241]:
X_remainder, X_test, y_remainder, y_test = train_test_split(
    X,
    y,
    stratify=y,
    random_state=1337,
    test_size=0.2,
)
X_remainder.reset_index(drop=True, inplace=True)
X_test.reset_index(drop=True, inplace=True)
y_remainder.reset_index(drop=True, inplace=True)
y_test.reset_index(drop=True, inplace=True)

In [242]:
X_train, X_validation, y_train, y_validation = train_test_split(
    X_remainder,
    y_remainder,
    stratify=y_remainder,
    random_state=1337,
    test_size=0.2,
)
X_train.reset_index(drop=True, inplace=True)
X_validation.reset_index(drop=True, inplace=True)
y_train.reset_index(drop=True, inplace=True)
y_validation.reset_index(drop=True, inplace=True)

In [243]:
y_train

phishing
0            0
1            0
2            0
3            0
4            0
5            0
6            1
7            0
8            0
9            0
10           0
11           1
12           0
13           0
14           0
15           1
16           0
17           0
18           1
19           1
20           1
21           0
22           0
23           1
24           0
25           1
26           0
27           0
28           1
29           0
30           1
31           1
32           0
33           0
34           0
35           1
36           0
37           1
38           0
39           1
40           1
41           0
42           1
43           1
44           0
45           1
46           0
47           0
48           1
49           1
50           0
51           0
52           1
53           0
54           1
55           0
56           0
57           1
58           0
59           0
60           1
61           1
62           0
63           0
64           1
65           0
66           1
67           1
68           0
69           1
70           0
71           1
72           1
73           0
74           1
75           0
76           1
77           0
78           0
79           1
80           0
81           0
82           0
83           1
84           1
85           0
86           1
87           0
88           0
89           0
90           1
91           0
92           0
93           0
94           0
95           1
96           0
97           1
98           1
99           0
100          0
101          0
102          1
103          0
104          0
105          1
106          1
107          0
108          1
109          0
110          0
111          1
112          0
113          1
114          0
115          0
116          1
117          0
118          1
119          0
120          0
121          1
122          0
123          0
124          1
125          1
126          0
127          0
128          0
129          1
130          1
131          1
132          1
133          1
134          1
135          1
136          0
137          1
138          0
139          0
140          1
141          1
142          1
143          1
144          0
145          0
146          1
147          1
148          1
149          0
150          1
151          0
152          1
153          1
154          1
155          1
156          1
157          1
158          0
159          0
160          0
161          1
162          0
163          0
164          1
165          0
166          1
167          0
168          0
169          1
170          0
171          0
172          0
173          0
174          1
175          0
176          0
177          0
178          1
179          1
180          1
181          0
182          0
183          1
184          1
185          1
186          0
187          0
188          1
189          0
190          1
191          0
192          0
193          1
194          1
195          1
196          0
197          1
198          1
199          0
200          1
201          0
202          0
203          0
204          0
205          0
206          0
207          1
208          1
209          1
210          1
211          1
212          0
213          1
214          0
215          1
216          1
217          0
218          1
219          0
220          1
221          0
222          1
223          1
224          0
225          0
226          1
227          0
228          0
229          0
230          0
231          0
232          0
233          0
234          0
235          0
236          1
237          1
238          0
239          1
240          1
241          0
242          1
243          1
244          0
245          0
246          0
247          0
248          1
249          0
250          0
251          1
252          1
253          1
254          1
255          0
256          0
257          1
258          1
259          1
260          1
261          0
262          1
263          0
264          1
265          0
2

In [244]:
X_train[y_train['phishing'] == 1]

content  unsecure_link_count  \
6     THANKS JOE M Do you Yahoo Yahoo High quality x...                    1   
11    FROM THE DESK OF AUDITOR OF STANDARD EXCITE WE...                    0   
15    DEAR BELOVED AND COMPLIMENT OF THE SEASON I AM...                    0   
18    from and of s family to hear f you Reply me an...                    0   
19                                in R S in in in in in                    0   
20    ME PLAIT NE AI ATTENTION POUR M AIDER A LA SEP...                    0   
23    Protect Your Account Make sure you never provi...                    1   
25    aW gaW IE h l gaW b aW b b N b c b b l aW Nob ...                    0   
28    FROM AKRA MISS KRA OF LATE KRA FORMER FINANCIA...                    0   
30    Dear sir Thank you for your recent Refinance A...                    0   
31    NOTICE Suspicious Activity Account Suspended D...                    1   
35    To report please visit our site at abuse Your ...                    5   
37    VICTOR CORP Dear sir I am the chief engineer a...                    0   
39    Dear Sir I am a Barrister and a member of Your...                    0   
40    so that I can provide you with for the release...                    0   
42    From D Bank D D AA Street D Zone D D A D PROPO...                    0   
43    Youve added an additional address to your acco...                    0   
45    Your registered name is included to show this ...                    2   
48    I am Mary from I am married to who worked as t...                    0   
49    One Come across your profile and have Decided ...                    0   
52    Hello I got your address through search in the...                    0   
54    of The Bank Two Exchange Square Connaught Plac...                    0   
57    am sure that this letter will come to you as a...                    0   
60    Rainbow International Sir It me the responsibi...                    0   
61    BANK BRANCH CENTRAL HONG HONK Dear Sir Let me ...                    1   
64    FROM SOUTH THE DIRECTOR APPEAL FOR ASSISTANCE ...                    0   
66    in treat with a honest greeting to you and you...                    2   
67    From Guest Hotel Number APPEAL FOR URGENT ASSI...                    0   
69    FROM MISS A E Beloved one Based on your profil...                    0   
71    From My you is based on trust E I have seen wa...                    0   
72    Park South Copy To Of The Day Permit me to int...                    1   
74    Good day I know this mail might come to you as...                    0   
76    Dear National City business client The Nationa...                    1   
79    Office of bank Manager Street W N Friend I am ...                    0   
83    Dear National City business client The Nationa...                    1   
84    Dear business client of Bank The Customer Serv...                    1   
86    OWNER YOU FOR US It is from the that to commen...                    0   
90    I am Provincial Director Standard Bank of Sout...                    0   
95    UNITED ONLY TO A SAFE ACCOUNT Sir It is my ple...                    0   
97    AND EXCHANGE REPUBLIC OF am the manager of bil...                    0   
98    Dear National City business client The Nationa...                    1   
102   International Remittance Department Bank Limit...                    0   
105   ONE Is my pleasure to inform you of my desire ...                    0   
106   in the Lord to you and your family I am from I...                    0   
108   Dear T business client The T Customer Service ...                    1   
111   h maybe legally confidential discrete and or p...                    0   
113   Dear Friend My name is Cole a senior staff and...                    0   
116   Dear Community We have decided to close on due...                    0   
118   RIGHT OF I strongly regret any inconvenience t...                    0   
121   Dear Mutual Cardholder We regret to inform

In [245]:
X_test[y_test['phishing'] == 1]

content  unsecure_link_count  \
6     DEAR SIR STRICTLY PRIVATE AND CONFIDENTIAL You...                    0   
7     My c Z b b Y V l b l ya F c V d b x b l V aW b...                    0   
8     Untitled Document Dear Customer As part of our...                    0   
9     URGENT TRANSFER Good Day My Dear We want to tr...                    0   
12    UNION BANK OF BANK ISLAND REPLY TO MY BOX BUSI...                    0   
15    VERY A E AM THE MANAGER OF AND EXCHANGE AT THE...                    0   
17    New Unpaid Item Message from response Dear mem...                    0   
18    Untitled Document Your credit card account hig...                    0   
19                                                    p                    0   
20    The President Sir Madam It is indeed my pleasu...                    0   
21    Dear Friend My name is I am a staff of NA with...                    0   
22    Untitled Document from Your bank us regarding ...                    0   
24    New Page Survey Center Advisory You have been ...                    1   
25    FROM THE DESK OF AUDIT AND ACCOUNTING BANK INT...                    1   
26    Good afternoon unfortunately some have been cr...                    0   
30    In attention of all Credit Union screening the...                    0   
36    Number Complete the above and send back to me ...                    0   
40    pIC b b aW J aW ga b aW V V Y c R b J haW c c ...                    0   
42    Please verify your account Your Account is Blo...                    0   
43    Dear customer As the and information technolog...                    0   
44    PLEASE HELP ME Dear Friend You may be to recei...                    1   
45    Dear I know this letter will come to you as su...                    0   
51    Happy day I am Peter a staff of the finance Pl...                    0   
54    OFFICE OF MINISTRY OF WORKS AND THE PRESIDENT ...                    0   
55    Dear Friend With due respect I like to disclos...                    0   
56    Notification of Limited Account Access As part...                    0   
58    GROUP NATIONAL PETROLEUM DIRECTOR DEAR SIR MY ...                    0   
61    STRICTLY CONFIDENTIAL FROM THE DESK OF AND ACC...                    1   
62                          This mail sent through zoom                    1   
64    Banking Dear Sir Madam Bank is to announce abo...                    1   
73    Larry Brown Dear Sir Madam RE INVESTMENT My ar...                    0   
74    My name is AL wife of AL the former minister f...                    1   
78    license and foreign account because this sum i...                    0   
80    NO DRIVE INDEPENDENCE LAY OUT STATE VERY URGEN...                    0   
81    Any can but it a real to But they need to reme...                    1   
82    Content transfer printable sent this message t...                    7   
85    Dear Sir I got your contact from our Chamber o...                    2   
87    Good Day Dear Friend My name is manager credit...                    0   
91    You may or may not have of me however been mar...                    0   
92    Untitled Document Dear Valued Customer As part...                    0   
101   From the Desk of General International Commerc...                    0   
102   SIR I WRITE TO YOU OF A MATTER THAT AN WITH TO...                    1   
104   Dear Sir REQUEST FOR YOUR UNRESERVED ASSISTANC...                    0   
106   Accountant General Natural Gas Dear want to be...                    0   
107   PETER Dear Friend Do accept my sincere if my m...                    0   
108   Untitled Document Dear valued customer We regr...                    0   
111   From Desk Audit Avenue Plateau Cote D Subject ...                    0   
112   proposition para c la situation traverse m a e...                    0   
113   OFFICE OF THE REVIEW PANEL E A A AM THE ORDINA...                    0   
115   Security Center Advisory We recently one o

In [247]:
phishing_df = X_train[y_train['phishing'] == 1].reset_index(drop=True)
ham_df = X_train[y_train['phishing'] == 0].reset_index(drop=True)

In [248]:
# import the nltk stopwords
nltk.download('stopwords')
from nltk.corpus import stopwords 

ENGLISH_STOP_WORDS = stopwords.words('english')
stemmer = nltk.stem.PorterStemmer()

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/rosswillett/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [249]:
def custom_tokenizer(text):
    # allow alphabetical characters and spaces only
    processed_text = re.sub(r'[^a-zA-Z\s]', '', text)
    # Filter out additional spaces
    processed_text = re.sub(r'\s\s*', ' ', processed_text)
    # Filter out weird symbols i.e. "1x2"
    processed_text = re.sub(r'\d*x\d*', '', processed_text)
    
    # split sentence into words
    listofwords = processed_text.split(' ')
    listofstemmed_words = []
    
    # remove stopwords and any tokens that are just empty strings
    for word in listofwords:
        if (not word in ENGLISH_STOP_WORDS) and (word!=''):
            # Stem words
            stemmed_word = stemmer.stem(word)
            listofstemmed_words.append(stemmed_word)

    return listofstemmed_words

## Analyzing Email Words

### Analyzing Top Phishing Words

In [267]:
phishing_word_vectorizer = CountVectorizer(
    tokenizer=custom_tokenizer,
    min_df=0.1,
)
phishing_word_vectorizer.fit(phishing_df['content'])
phishing_word_vectorized = phishing_word_vectorizer.transform(phishing_df['content'])

In [268]:
phishing_word_df = pd.DataFrame(
    data=phishing_word_vectorized.toarray(),
    columns=phishing_word_vectorizer.get_feature_names_out(),
)
phishing_word_sum_df = pd.DataFrame(
    {"counts": phishing_word_vectorized.toarray().sum(axis=0)},
    index=phishing_word_vectorizer.get_feature_names_out(),
).sort_values("counts", ascending=False)

In [269]:
phishing_word_df

accept  access  accord  account  address  agre  also  amount  arrang  \
0          0       0       0        0        0     0     0       0       0   
1          0       0       0       13        1     0     0       2       0   
2          0       0       0        0        2     0     1       3       0   
3          0       0       0        0        0     0     0       0       0   
4          0       0       0        0        0     0     0       0       0   
...      ...     ...     ...      ...      ...   ...   ...     ...     ...   
3750       0       0       0        1        0     0     0       0       0   
3751       0       0       0        0        0     0     0       0       0   
3752       0       0       0        0        0     0     0       0       0   
3753       1       0       0        3        0     0     2       2       0   
3754       0       0       1        6        0     1     0       1       0   

      ask  assist  assur  attent  b  back  bank  base  believ  beneficiari  \
0       0       0      0       0  0     0     0     0       0            0   
1       1       1      1       0  2     0     8     0       2            1   
2       0       2      0       0  0     0     0     0       0            0   
3       0       0      0       0  1     0     0     0       0            0   
4       0       0      0       0  0     0     0     0       0            0   
...   ...     ...    ...     ... ..   ...   ...   ...     ...          ...   
3750    0       0      0       0  0     0     1     0       0            0   
3751    0       0      0       0  1     0     0     0       0            0   
3752    1       0      0       0  0     0     2     0       0            0   
3753    0       2      1       0  0     0     1     0       0            0   
3754    1       2      1       0  0     0     8     0       0            0   

      best  bless  busi  c  choos  claim  click  client  come  commun  \
0        0      0     0  0      0      0      0       0     0       0   
1        0      0     4  2      0      0      0       0     0       0   
2        1      0     2  0      0      0      0       0     0       1   
3        0      1     0  1      0      0      0       0     0       0   
4        0      0     0  0      0      0      0       0     0       0   
...    ...    ...   ... ..    ...    ...    ...     ...   ...     ...   
3750     0      0     0  0      0      0      0       0     0       0   
3751     0      0     0  2      0      0      0       0     0       0   
3752     0      0     0  0      0      0      1       0     0       0   
3753     0      0     1  0      0      0      0       0     0       0   
3754     0      1     1  0      0      1      0       4     1       0   

      compani  complet  confid  confidenti  confirm  contact  corpor  could  \
0           0        0       0           0        0        0       0      0   
1           0        0       1           1        1        1       0      0   
2           0        0       0           3        1        1       0      0   
3           0        0       0           0        0        0       0      0   
4           0        0       0           0        0        0       0      0   
...       ...      ...     ...         ...      ...      ...     ...    ...   
3750        0        0       0           0        0        3       0      0   
3751        0        0       0           0        0        0       0      0   
3752        0        0       0           0        1        0       0      0   
3753        1        0       1           2        0        0       0      0   
3754        0        0       1           0        0        2       0      1   

      countri  crash  custom  day  deal  dear  death  deceas  decid  depart  \
0           0      0       0    0     0     0      0       0      0       0   
1           2      0       0    1     1     1      1       0      0       0   
2           3      0       0    1     0     1      1       0      1  

In [270]:
phishing_word_sum_df

counts
e             13797
account        8855
bank           6889
money          6213
us             4737
fund           4688
pleas          3884
busi           3470
inform         3140
secur          3028
transact       2950
b              2913
transfer       2906
foreign        2903
f              2903
assist         2851
million        2725
countri        2708
c              2523
net            2470
contact        2286
mail           2154
kin            2132
compani        2126
person         1899
one            1892
want           1871
n              1863
address        1840
help           1765
sum            1753
name           1743
r              1733
invest         1723
dear           1718
may            1705
also           1669
famili         1656
receiv         1594
know           1571
repli          1553
late           1497
u              1493
use            1447
need           1446
come           1445
work           1439
sinc           1421
father         1390
claim          1350
thank          1311
would          1309
make           1303
immedi         1298
unit           1293
send           1262
go             1261
servic         1250
govern         1240
interest       1235
privat         1219
custom         1215
get            1215
number         1213
confidenti     1202
soon           1158
provid         1146
time           1122
death          1109
decid          1090
made           1081
give           1071
protect        1066
respons        1064
access         1057
shall          1041
deposit        1031
total          1029
click          1015
day            1004
manag           988
god             988
trust           975
forward         961
amount          959
urgent          949
sent            946
present         943
due             909
free            896
five            896
take            870
telephon        864
nation          861
propos          858
confirm         856
hundr           851
partner         849
like            845
deceas          844
new             828
good            814
client          808
son             804
depart          796
safe            794
oper            787
look            778
beneficiari     769
follow          758
letter          757
upon            756
share           748
updat           744
got             743
link            741
without         740
best            725
first           722
seek            721
commun          719
messag          714
presid          711
thousand        709
sir             702
enabl           701
posit           693
sincer          686
success         683
corpor          682
world           665
assur           663
risk            657
necessari       656
payment         644
discov          642
state           639
deal            639
life            637
form            633
back            631
must            627
full            624
offic           619
therefor        614
two             612
keep            606
eecut           605
understand      602
possibl         599
believ          597
visit           586
request         581
recent          581
live            581
th              580
accord          579
crash           579
law             575
involv          575
well            573
member          572
hear            571
matter          569
complet         559
respect         552
let             545
note            542
phone           541
accept          533
part            533
way             523
friend          522
still           522
confid          522
within          521
end             520
leav            520
reliabl         516
intern          513
order           510
wish            508
bless           505
agre            502
write           502
henc            501
last            494
stand           492
process         468
attent          466
support         460
arrang          458
set             458
offer           452
could           445
base            442
reason          441
year            441
howev           438
choos        

In [54]:
top_phish_words_df = phishing_word_df.loc[:,phishing_word_sum_df.index]

### Analyzing Top Ham Emails

In [65]:
ham_word_vectorizer = CountVectorizer(
    tokenizer=custom_tokenizer,
    min_df=0.1,
)
ham_word_vectorizer.fit(ham_df['content'])
ham_word_vectorized = ham_word_vectorizer.transform(ham_df['content'])

In [66]:
ham_word_df = pd.DataFrame(
    data=ham_word_vectorized.toarray(),
    columns=ham_word_vectorizer.get_feature_names_out(),
)
ham_word_sum_df = pd.DataFrame(
    {"counts": ham_word_vectorized.toarray().sum(axis=0)},
    index=ham_word_vectorizer.get_feature_names_out(),
).sort_values("counts", ascending=False)

In [69]:
ham_word_df

2002  also  call  could  dont  email  get  go  good  group  ...  time  \
0        1     0     1      0     0      2    3   1     0      0  ...     0   
1        0     0     0      0     0      0    1   0     0      0  ...     0   
2        0     1     1      0     0      0    0   0     0      0  ...     0   
3        0     0     2      0     0      0    0   1     0      0  ...     1   
4        0     0     0      0     0      1    1   1     0      0  ...     0   
...    ...   ...   ...    ...   ...    ...  ...  ..   ...    ...  ...   ...   
7965     0     0     0      0     0      0    0   1     0      1  ...     0   
7966     0     0     0      1     0      0    0   0     1      0  ...     0   
7967     0     0     0      0     0      0    0   0     0      0  ...     1   
7968     0     0     0      0     0      0    0   0     0      0  ...     0   
7969     0     0     0      0     0      0    0   0     0      0  ...     0   

      tri  use  user  want  way  well  work  would  wrote  
0       0    0     1     0    0     0     0      1      1  
1       0    0     0     0    0     0     0      0      0  
2       0    0     0     0    0     0     1      0      0  
3       0    0     0     0    0     0     0      0      0  
4       0    0     0     0    0     0     0      0      0  
...   ...  ...   ...   ...  ...   ...   ...    ...    ...  
7965    0    0     1     1    0     0     4      2      0  
7966    0    0     0     0    0     0     0      0      0  
7967    0    0     0     1    0     0     0      0      0  
7968    0    0     0     0    0     0     0      0      0  
7969    0    0     0     0    0     0     0      0      0  

[7970 rows x 37 columns]

In [67]:
ham_word_sum_df

counts
use       3886
get       3043
one       3007
list      2964
would     2610
like      2514
new       2501
work      2465
time      2452
2002      2250
email     2198
mail      2108
make      1972
messag    1832
dont      1756
also      1752
need      1675
go        1664
group     1651
want      1651
inform    1627
say       1623
call      1597
wrote     1572
im        1563
know      1536
see       1523
linux     1520
user      1509
think     1482
way       1378
look      1372
right     1364
could     1350
well      1255
good      1181
tri       1124

### Analyzing Phishing NGrams

In [58]:
phishing_ngram_vectorizer = CountVectorizer(
    tokenizer=custom_tokenizer,
    min_df=10,
    ngram_range=(2, 3),
)
phishing_ngram_vectorizer.fit(phishing_df['content'])
phishing_ngram_vectorized = phishing_ngram_vectorizer.transform(phishing_df['content'])

In [59]:
phishing_ngram_df = pd.DataFrame(
    {"counts": phishing_ngram_vectorized.toarray().sum(axis=0)},
    index=phishing_ngram_vectorizer.get_feature_names_out(),
).sort_values("counts", ascending=False)

In [60]:
phishing_ngram_df.head(30)

counts
next kin               2197
unit state             1255
bank account           1080
email address          1020
secur compani           941
hundr thousand          770
state dollar            758
unit state dollar       715
fax number              644
south africa            641
transfer money          603
paypal account          591
pleas repli             534
look forward            526
foreign account         512
five hundr              508
million unit            507
would like              507
account access          496
transfer fund           483
telephon fax            462
million unit state      459
custom servic           453
million five            450
five hundr thousand     442
plane crash             438
thousand unit           434
kin relat               428
total sum               425
repli email             420

### Analyzing Ham NGrams

In [61]:
ham_ngram_vectorizer = CountVectorizer(
    tokenizer=custom_tokenizer,
    min_df=10,
    ngram_range=(2, 3),
)
ham_ngram_vectorizer.fit(ham_df['content'])
ham_ngram_vectorized = ham_ngram_vectorizer.transform(ham_df['content'])

In [62]:
ham_ngram_df = pd.DataFrame(
    {"counts": ham_ngram_vectorized.toarray().sum(axis=0)},
    index=ham_ngram_vectorizer.get_feature_names_out(),
).sort_values("counts", ascending=False)

In [63]:
ham_ngram_df.head(30)

counts
mail list                                             1178
linux user                                             682
user group                                             665
linux user group                                       663
irish linux                                            661
irish linux user                                       661
list maintain                                          659
inform list maintain                                   659
unsubscript inform                                     659
unsubscript inform list                                659
inform list                                            659
list maintain listmasterlinuxi                         657
maintain listmasterlinuxi                              657
user group iluglinuxi                                  615
group iluglinuxi httpwwwlinuxiemailmanlistinfoilug     615
iluglinuxi httpwwwlinuxiemailmanlistinfoilug un...     615
httpwwwlinuxiemailmanlistinfoilug unsubscript          615
group iluglinuxi                                       615
httpwwwlinuxiemailmanlistinfoilug unsubscript i...     615
iluglinuxi httpwwwlinuxiemailmanlistinfoilug           615
sfnet email sponsor                                    453
sfnet email                                            453
email sponsor                                          453
unit state                                             437
rpmlist mail                                           351
rpmlist mail list                                      351
email address                                          350
list httplistsfreshrpmsnetmailmanlistinforpmlist       348
mail list httplistsfreshrpmsnetmailmanlistinfor...     348
razorus mail                                           259

## Vectorize All Emails

## Building Initial Models

In [250]:
email_word_vectorizer = CountVectorizer(
    tokenizer=custom_tokenizer,
    min_df=0.01
)
email_word_vectorizer.fit(X_train['content'])
email_word_vectorized = email_word_vectorizer.transform(X_train['content'])

In [251]:
cv_transf = ColumnTransformer([
        (
            'count_vectorizer',
            CountVectorizer(
                tokenizer=custom_tokenizer,
                min_df=0.01
            ),
            'content',
        )
    ],
    remainder='passthrough'
)

In [252]:
X_train = cv_transf.fit_transform(X_train)

In [253]:
X_train = pd.DataFrame(
    data=X_train.toarray(),
    columns=cv_transf.get_feature_names_out(),
)
X_train.head(10)

count_vectorizer__abandon  count_vectorizer__abil  count_vectorizer__abl  \
0                          0                       0                      0   
1                          0                       0                      0   
2                          0                       0                      0   
3                          0                       0                      0   
4                          0                       0                      0   
5                          0                       0                      0   
6                          0                       0                      0   
7                          0                       0                      0   
8                          0                       0                      0   
9                          0                       0                      0   

   count_vectorizer__abroad  count_vectorizer__absolut  \
0                         0                          0   
1                         0                          0   
2                         0                          0   
3                         0                          0   
4                         0                          0   
5                         0                          0   
6                         0                          0   
7                         0                          0   
8                         0                          0   
9                         0                          0   

   count_vectorizer__accept  count_vectorizer__access  \
0                         0                         0   
1                         0                         0   
2                         0                         0   
3                         0                         0   
4                         0                         0   
5                         0                         0   
6                         0                         0   
7                         0                         0   
8                         0                         0   
9                         0                         0   

   count_vectorizer__accid  count_vectorizer__accord  \
0                        0                         0   
1                        0                         0   
2                        0                         0   
3                        0                         0   
4                        0                         0   
5                        0                         0   
6                        0                         0   
7                        0                         0   
8                        0                         0   
9                        0                         0   

   count_vectorizer__accordingli  count_vectorizer__account  \
0                              0                          0   
1                              0                          0   
2                              0                          0   
3                              0                          0   
4                              0                          0   
5                              0                          0   
6                              0                          0   
7                              0                          0   
8                              0                          0   
9                              0                          0   

   count_vectorizer__achiev  count_vectorizer__acknowledg  \
0                         0                             0   
1                         0                             0   
2                         0                             0   
3                         0                             0   
4                         0                             0   
5                         0                             0   
6                         0                             0   
7                         0                             0   
8     

In [254]:
X_train.shape

(8336, 1161)

In [255]:
X_validation = cv_transf.transform(X_validation)
X_validation = pd.DataFrame(
    data=X_validation.toarray(),
    columns=cv_transf.get_feature_names_out(),
)
X_validation.head(10)

count_vectorizer__abandon  count_vectorizer__abil  count_vectorizer__abl  \
0                          0                       0                      0   
1                          0                       0                      0   
2                          0                       0                      0   
3                          0                       0                      0   
4                          0                       0                      0   
5                          0                       0                      0   
6                          0                       0                      0   
7                          0                       0                      0   
8                          0                       0                      0   
9                          0                       0                      0   

   count_vectorizer__abroad  count_vectorizer__absolut  \
0                         0                          0   
1                         0                          0   
2                         0                          0   
3                         0                          0   
4                         0                          0   
5                         0                          0   
6                         0                          0   
7                         0                          0   
8                         0                          0   
9                         0                          0   

   count_vectorizer__accept  count_vectorizer__access  \
0                         0                         0   
1                         0                         0   
2                         0                         0   
3                         0                         0   
4                         0                         0   
5                         0                         0   
6                         0                         0   
7                         0                         0   
8                         0                         0   
9                         0                         0   

   count_vectorizer__accid  count_vectorizer__accord  \
0                        0                         0   
1                        0                         0   
2                        0                         0   
3                        0                         0   
4                        0                         0   
5                        0                         0   
6                        0                         0   
7                        0                         0   
8                        0                         0   
9                        0                         0   

   count_vectorizer__accordingli  count_vectorizer__account  \
0                              0                          0   
1                              0                          0   
2                              0                          0   
3                              0                          0   
4                              0                          0   
5                              0                          0   
6                              0                          0   
7                              0                          6   
8                              0                          0   
9                              0                          0   

   count_vectorizer__achiev  count_vectorizer__acknowledg  \
0                         0                             0   
1                         0                             0   
2                         0                             0   
3                         0                             0   
4                         0                             0   
5                         0                             0   
6                         0                             0   
7                         0                             0   
8     

In [257]:
X_validation.shape

(2084, 1161)

In [258]:
log_reg_model = LogisticRegression()
log_reg_model.fit(X_train, y_train)
log_reg_model.score(X_train, y_train)

0.9745681381957774

In [259]:
log_reg_model.score(X_validation, y_validation)

0.9697696737044146

In [260]:
log_reg_coef_pd = pd.DataFrame(log_reg_model.coef_, columns=X_train.columns, index=['Coefficient']).T

In [262]:
log_reg_coef_pd.sort_values(by='Coefficient', ascending=False).head(20)

Coefficient
count_vectorizer__bank         1.934222
count_vectorizer__yahoo        1.633896
count_vectorizer__fund         1.512316
count_vectorizer__dear         1.449070
count_vectorizer__transact     1.306326
count_vectorizer__address      1.097540
count_vectorizer__respons      1.087400
count_vectorizer__l            1.082084
count_vectorizer__god          1.076197
count_vectorizer__sincer       1.069274
count_vectorizer__privat       1.042545
count_vectorizer__compani      1.037740
count_vectorizer__item         1.032132
count_vectorizer__repli        1.031066
count_vectorizer__money        1.030922
count_vectorizer__busi         1.029608
count_vectorizer__pleas        0.972397
count_vectorizer__card         0.943808
count_vectorizer__number       0.935830
count_vectorizer__bless        0.921920

In [263]:
minMaxScaler = MinMaxScaler()
minMaxScaler.fit(X_train)
x_mm_scaled = minMaxScaler.transform(X_train)
knn_model = KNeighborsClassifier(n_neighbors=5)
knn_model.fit(x_mm_scaled, y_train)
knn_model.score(x_mm_scaled, y_train)

0.900911708253359

In [264]:
x_mm_scaled = minMaxScaler.transform(X_validation)
knn_model = KNeighborsClassifier(n_neighbors=5)
knn_model.fit(x_mm_scaled, y_validation)
knn_model.score(x_mm_scaled, y_validation)

0.8642034548944337

In [265]:
dec_tree_model = DecisionTreeClassifier()
dec_tree_model.fit(X_train, y_train)
dec_tree_model.score(X_train, y_train)

0.9989203454894434

In [266]:
dec_tree_model.score(X_validation, y_validation)

0.9371401151631478

### Build Test Pipelines

In [ ]:
# combined_top_words_df = list(set(ham_word_sum_df.index.to_list() + phishing_word_sum_df.index.to_list()))
# combined_top_words_df

In [123]:
cachedir = mkdtemp()
mod_pipeline = Pipeline([
        ('vectorize', cv_transf),
        ('scaler', StandardScaler()),
        ('model', LogisticRegression())
    ],
    memory=cachedir
)

In [137]:
basic_model_cv = GridSearchCV(
    estimator=mod_pipeline,
    cv=5,
    param_grid=[
        {
            'scaler': [None, StandardScaler(), MinMaxScaler()],
            'model': [LogisticRegression()]
        },
        {
            'scaler': [StandardScaler(), MinMaxScaler()],
            'model': [KNeighborsClassifier()]
        },
        {
            'scaler': [None],
            'model': [DecisionTreeClassifier()]
        }
    ],
    verbose=2
)

In [138]:
basic_model_cv.fit(X_remainder, y_remainder)

Fitting 5 folds for each of 6 candidates, totalling 30 fits
[CV] END ............model=LogisticRegression(), scaler=None; total time=  33.7s
[CV] END ............model=LogisticRegression(), scaler=None; total time=  33.7s
[CV] END ............model=LogisticRegression(), scaler=None; total time=  33.7s
[CV] END ............model=LogisticRegression(), scaler=None; total time=  33.7s
[CV] END ............model=LogisticRegression(), scaler=None; total time=  33.7s
[CV] END model=LogisticRegression(), scaler=StandardScaler(); total time=  26.5s
[CV] END model=LogisticRegression(), scaler=StandardScaler(); total time=  26.7s
[CV] END model=LogisticRegression(), scaler=StandardScaler(); total time=  27.0s
[CV] END model=LogisticRegression(), scaler=StandardScaler(); total time=  27.7s
[CV] END model=LogisticRegression(), scaler=StandardScaler(); total time=  27.2s
[CV] END ..model=LogisticRegression(), scaler=MinMaxScaler(); total time=  26.6s
[CV] END ..model=LogisticRegression(), scaler=Min

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('vectorize',
                                        ColumnTransformer(transformers=[('count_vectorizer',
                                                                         CountVectorizer(min_df=0.01,
                                                                                         tokenizer=<function custom_tokenizer at 0x7f7979505510>),
                                                                         'content')])),
                                       ('scaler', StandardScaler()),
                                       ('model', LogisticRegression())]),
             param_grid=[{'model': [LogisticRegression()],
                          'scaler': [None, StandardScaler(), MinMaxScaler()]},
                         {'model': [KNeighborsClassifier()],
                          'scaler': [StandardScaler(), MinMaxScaler()]},
                         {'model': [DecisionTreeClassifier()],
                          'scaler': [None]}],
             verbose=2)

In [143]:
basic_model_cv.best_params_

{'model': LogisticRegression(), 'scaler': None}

In [141]:
basic_model_cv.best_score_

0.9505291563776448